In [0]:
from pyspark.ml.feature import StringIndexer
from pyspark.sql import functions as F
from pyspark.sql.window import Window

def fill_null_values(df):
    # Iterate through each column
    for col in df.columns:
        col_type = dict(df.dtypes)[col]
        
        if col_type in ['int', 'bigint', 'float', 'double', 'decimal']:  # Numeric columns
            # Fill numeric columns with the mean value or a default value if mean is null
            mean_value = df.select(F.mean(F.col(col))).first()[0]
            if mean_value is None:
                mean_value = 0  # Default value for numeric columns
            df = df.fillna({col: mean_value})
            print(f"Filled nulls in numeric column '{col}' with mean value: {mean_value}")
        
        elif col_type == 'string':  # String columns
            # Fill string columns with the most frequent value (mode) or a default value if mode is null
            mode_value = df.groupBy(col).count().orderBy(F.desc('count')).first()[0]
            if mode_value is None:
                mode_value = 'unknown'  # Default value for string columns
            df = df.fillna({col: mode_value})
            print(f"Filled nulls in string column '{col}' with mode value: {mode_value}")
    
    return df

# Define the list of table names you want to process
table_name = ['reviews', 'authors', 'products']  # Example table names

# Main code to read, transform, and write the data
for name in table_name:
    path = '/mnt/silver/dbo/' + name 
    print(path)
    df = spark.read.format('delta').load(path)

    # Remove 'skin_type' column if it exists
    if 'skin_type' in df.columns:
        df = df.drop('skin_type')
        print(f"'skin_type' column removed from {name}")
    
    # Fill null values before encoding
    df = fill_null_values(df)
    
    # Encoding columns: 'skin_tone', 'eye_color', 'hair_color', 'product_id'
    columns_to_encode = ['skin_tone', 'eye_color', 'hair_color', 'product_id']
    
    for col in columns_to_encode:
        if col in df.columns:
            indexer = StringIndexer(inputCol=col, outputCol=col + '_encoded', handleInvalid='keep')
            df = indexer.fit(df).transform(df)
            print(f"Encoded column '{col}' in {name} and added '{col}_encoded'")
    
    # Save the transformed data to the gold layer
    output_path = '/mnt/gold/dbo/' + name + '/'
    df.write.format('delta') \
        .mode('overwrite') \
        .option("overwriteSchema", "true") \
        .save(output_path)
    print(f"Table {name} processed and saved to {output_path}")

/mnt/silver/dbo/reviews
Filled nulls in string column 'product_id' with mode value: P420652
Filled nulls in string column 'author_id' with mode value: 1696370280
Filled nulls in numeric column 'rating' with mean value: 4.311837975188082
Filled nulls in numeric column 'is_recommended' with mean value: 0.8379222687168313
Filled nulls in numeric column 'helpfulness' with mean value: 0.7697218318146404
Filled nulls in numeric column 'total_feedback_count' with mean value: 3.6606613189842725
Filled nulls in numeric column 'total_pos_feedback_count' with mean value: 2.895188746616179
Filled nulls in numeric column 'total_neg_feedback_count' with mean value: 0.7654725723680933
Filled nulls in string column 'review_text' with mode value: unknown
Filled nulls in string column 'review_title' with mode value: unknown
Filled nulls in numeric column 'ID' with mean value: 301065.5
Encoded column 'product_id' in reviews and added 'product_id_encoded'
Table reviews processed and saved to /mnt/gold/dbo

In [0]:
display(spark.read.format('delta').load('/mnt/gold/dbo/reviews/'))

product_id author_id rating is_recommended helpfulness total_feedback_count total_pos_feedback_count total_neg_feedback_count submission_time review_text review_title ID product_id_encoded P478030 5558293249 3 1.0 0.0 4 0 4 2022-06-25 Very thick cleanser. Barely any scent. Very moisturizing. Cleans face well. Do not like that a tiny bit gets in my eyes and makes my vision cloudy. As much as i rub it with water, and then rinse it off, i still get a bid of cloudyness. I would see myself using this more in the winter. Careful with eyes 1 51.0 P478030 24961612421 1 0.0 0.800000011920929 5 4 1 2022-06-25 It doesn’t leave skin!!!!! You need another product to be used multiple times to get rid of this layer nope 2 51.0 P478030 2529971806 1 0.0 0.0 1 0 1 2022-06-25 I would give this 0 if I could it broke me out so bad I thought I had chicken pocks, I have never broken out for a. Skin care product before and have loved previous items by this brand but this was horrible. don’t do it 3 51.0 P478030 8106375892 2 0.0 0.5 2 1 1 2022-06-24 I didn’t love how this made my skin feel. It felt hard to get off. I’m probably just not a fan of balm cleansers so if you prefer them you might like it more than me. unknown 4 51.0 P478030 12404762520 1 0.0 0.5 2 1 1 2022-06-24 I thought I’d try this because it’s so affordable. The product I received feels separated. Part of it goes on thick like Vaseline, and then while I’m squeezing the thick part out, a thin drizzle of oil leaks everywhere. It doesn’t melt and spread easily so I feel like I’m pulling at my skin unnecessarily when I cleanse with this. Somehow, I still always have raccoon eyes afterward and have to go in with another makeup removed. As others have mentioned, this leaves a very oily residue that is hard to wash off after. There are way better cleansing balms out there. Doesn’t “melt”, product separates 5 51.0 P478030 24580957046 4 1.0 1.0 1 1 0 2022-06-24 The product is great for the price! The bottle lasted for months and I used up the entire bottle but did not repurchase because it does not wash off as easily compared to what I normally use as a first step. unknown 6 51.0 P478030 33959812167 5 1.0 1.0 1 1 0 2022-06-23 Very gentle cleanser. Good at getting sunscreen off as a pre cleanser. A little goes a long way. best pre-cleanser I’ve used 7 51.0 P478030 24164706107 3 0.0 1.0 1 1 0 2022-06-23 Takes a while to get off the skin and I felt like it clogged my pores. Best to remove make up but maybe have a really good cleanser and toner to remove all residue. unknown 8 51.0 P478030 38044985271 5 1.0 0.0 1 0 1 2022-06-23 Personally I love this face wash! It works great and leaves my face feeling smooth. I would recommend to people without oily skin as it also works as a makeup remover and has some oils to help with that. awesome feeling 9 51.0 P478030 913940464 3 1.0 0.0 2 0 2 2022-06-22 I like it but it doesn’t rinse off completely. It leaves an oily residue. Fortunately I only use as.a first cleanser. My double cleanser usually gets off anything left behind by this. Also when I press the tube to get product out, I feel like the oil has separated from what is supposed to be a gel like consistency. It's good but confusing... 10 51.0 P173726 5159778305 5 1.0 0.7697218318146404 0 0 0 2018-11-07 The best facial cotton you will ever use. Soft and luxurious. Soft 11 63.0 P478030 36331452993 5 1.0 0.7697218318146404 0 0 0 2022-06-22 Great first step in skin routine to remove makeupIt helped my skin reduce redness after a ance breakout I’m guessing from the oats antioxidants which I love!! unknown 12 51.0 P478030 5476059198 4 1.0 1.0 2 2 0 2022-06-21 Ive been using this for over a year as my first cleanse. I have no complaints except for one thing - it leaves an oily residue. Doesn’t matter how long you rinse, it’s there. But that doesn’t really matter because it’s gone after my second cleanse. Im rating this a 3 star + 1 star because it’s hella cheap and does what a first cleanse does and doesn’t 

In [0]:
display(spark.read.format('delta').load('/mnt/gold/dbo/authors/'))

author_id skin_tone eye_color hair_color skin_tone_encoded eye_color_encoded hair_color_encoded 10000015049 fair green brown 2.0 3.0 0.0 10000060335 fair blue blonde 2.0 1.0 1.0 10000098796 unknown brown brown 0.0 0.0 0.0 1000010050 unknown brown brown 0.0 0.0 0.0 10000117144 light brown brown 1.0 0.0 0.0 10000120301 lightMedium green blonde 3.0 3.0 1.0 10000217994 fair brown red 2.0 0.0 4.0 10000247828 mediumTan green black 5.0 3.0 2.0 10000254625 fairLight Grey red 6.0 4.0 4.0 10000290716 light blue blonde 1.0 1.0 1.0 10000427309 tan brown black 7.0 0.0 2.0 10000569316 lightMedium brown brown 3.0 0.0 0.0 10000578851 light brown auburn 1.0 0.0 3.0 10000593839 fair blue red 2.0 1.0 4.0 10000688982 mediumTan brown blonde 5.0 0.0 1.0 10000689183 fairLight green blonde 6.0 3.0 1.0 10000697461 lightMedium brown brown 3.0 0.0 0.0 10000766339 medium brown black 4.0 0.0 2.0 10000770719 light brown brown 1.0 0.0 0.0 10000800079 fair brown brown 2.0 0.0 0.0 10000892274 lightMedium green blonde 3.0 3.0 1.0 10000898917 unknown brown brown 0.0 0.0 0.0 1000094971 light green red 1.0 3.0 4.0 1000095639 unknown brown brown 0.0 0.0 0.0 1000098116 fair brown brown 2.0 0.0 0.0 10001065571 fair brown red 2.0 0.0 4.0 10001148316 light brown brown 1.0 0.0 0.0 10001228964 fair green brunette 2.0 3.0 5.0 10001355168 light green red 1.0 3.0 4.0 10001355427 mediumTan brown black 5.0 0.0 2.0 10001367553 fairLight hazel brown 6.0 2.0 0.0 10001502449 light blue blonde 1.0 1.0 1.0 10001524132 unknown brown brown 0.0 0.0 0.0 10001606143 porcelain hazel brunette 11.0 2.0 5.0 10001621302 light brown blonde 1.0 0.0 1.0 1000163358 light brown brown 1.0 0.0 0.0 10001720125 medium brown black 4.0 0.0 2.0 10001723410 lightMedium brown brown 3.0 0.0 0.0 10001729300 medium brown brown 4.0 0.0 0.0 10001768414 light brown brunette 1.0 0.0 5.0 10001961830 light hazel blonde 1.0 2.0 1.0 10002123851 deep brown black 8.0 0.0 2.0 10002261835 light brown brown 1.0 0.0 0.0 1000235057 lightMedium brown black 3.0 0.0 2.0 10002552379 fair hazel black 2.0 2.0 2.0 10002642829 fairLight green auburn 6.0 3.0 3.0 10002646684 unknown brown brown 0.0 0.0 0.0 10002661574 lightMedium hazel blonde 3.0 2.0 1.0 1000284455 lightMedium brown brown 3.0 0.0 0.0 1000296322 lightMedium brown brown 3.0 0.0 0.0 1000312590 unknown brown brown 0.0 0.0 0.0 1000315494 fair brown brown 2.0 0.0 0.0 10003429784 unknown brown brown 0.0 0.0 0.0 10003432083 light brown brown 1.0 0.0 0.0 10003432615 medium brown brown 4.0 0.0 0.0 10003441511 light green brown 1.0 3.0 0.0 10003484761 fairLight brown black 6.0 0.0 2.0 1000362386 unknown brown brown 0.0 0.0 0.0 1000362738 unknown brown brown 0.0 0.0 0.0 1000373093 fair brown blonde 2.0 0.0 1.0 10003746636 light brown brown 1.0 0.0 0.0 10003785524 unknown brown brown 0.0 0.0 0.0 10003786534 fair blue brown 2.0 1.0 0.0 10003862770 lightMedium brown black 3.0 0.0 2.0 10003868106 light blue blonde 1.0 1.0 1.0 10004120452 deep brown black 8.0 0.0 2.0 10004120798 medium blue brown 4.0 1.0 0.0 10004120934 light brown black 1.0 0.0 2.0 10004121442 lightMedium brown brown 3.0 0.0 0.0 10004121688 deep brown black 8.0 0.0 2.0 10004122080 lightMedium hazel blonde 3.0 2.0 1.0 10004122562 light hazel brown 1.0 2.0 0.0 10004122637 unknown brown black 0.0 0.0 2.0 10004123308 fairLight blue brown 6.0 1.0 0.0 10004127103 fair blue brown 2.0 1.0 0.0 10004127873 light blue blonde 1.0 1.0 1.0 10004128082 deep brown black 8.0 0.0 2.0 10004128632 light blue brown 1.0 1.0 0.0 10004130889 medium blue blonde 4.0 1.0 1.0 10004131906 unknown brown brown 0.0 0.0 0.0 10004132091 light blue brown 1.0 1.0 0.0 10004132675 lightMedium brown brown 3.0 0.0 0.0 10004132823 fair blue brown 2.0 1.0 0.0 10004133205 fair green brown 2.0 3.0 0.0 10004133668 fair hazel brown 2.0 2.0 0.0 10004133982 fair blue brown 2.0 1.0 0.0 10004134298 light hazel brown 1.0 2.0 0.0 10004134499 light blue blonde 1.0 1.0 1.0 10004134520 light green blonde 1.0 3.0 1.0 10004138012 fairLight blue blonde 6.0 1.0 1.0 100041